## Import Dependencies

In [1]:
import pandas as pd
import math
import numpy as np
import matplotlib.pyplot as plt
import glob
import os
import time as time

## Read Comments
## Drop Unnessessary Column
## Use Ceiling function to Return the Rating as an Integer

In [2]:
comments = pd.read_csv('../data/large_sample.csv')
comments.drop(columns=['Unnamed: 0'], inplace=True)
comments.rating = np.ceil(comments.rating)

In [4]:
comments.head()

commenter  gameID  rating  \
0     172640   24068     7.0   
1      86674   24068     7.0   
2      10643   24068     7.0   
3      31171   24068     7.0   
4     165608   24068     7.0   

                                             comment  
0  Good:  Unique take on the hidden role games. T...  
1  A neat social deduction game with multiple tea...  
2  Good hidden roles werewolf style game that can...  
3  Overall I hate Mafia/Werewolf, but this versio...  
4  Fun social deduction exercise that gets merrie...

## Remove Punctuation
## Remove Uppercase

In [7]:
## return a string in lower case
def make_it_lower(comment):
    new_comment = []
    for x in comment.split(' '):
        new_comment.append(x.lower())
    return ' '.join(new_comment)

## remove punctuation
def remove_punctuation(comment):
    table = str.maketrans(dict.fromkeys('@#$%^&*()_+=~`[{}]|\:;"<,>."/'))
    return comment.translate(table)

## replace punctuation
def replace_exclimation(comment):
    return comment.replace('!', ' <!> ').replace('?', ' <?> ')

In [8]:
comments['lower_comment'] = comments.comment.apply(lambda x: make_it_lower(x))
comments.drop(columns=['comment'], inplace=True)
comments.rename(columns={'lower_comment':'comment'}, inplace=True)
comments['remove_punctuation'] = comments.comment.apply(lambda x: remove_punctuation(x))
comments.drop(columns=['comment'], inplace=True)
comments.rename(columns={'remove_punctuation':'comment'}, inplace=True)
comments['replace_punctuation'] = comments.comment.apply(lambda x: replace_exclimation(x))
comments.drop(columns=['comment'], inplace=True)
comments.rename(columns={'replace_punctuation':'comment'}, inplace=True)

In [10]:
comments.head()

commenter  gameID  rating  \
0     172640   24068     7.0   
1      86674   24068     7.0   
2      10643   24068     7.0   
3      31171   24068     7.0   
4     165608   24068     7.0   

                                             comment  
0  good  unique take on the hidden role games the...  
1  a neat social deduction game with multiple tea...  
2  good hidden roles werewolf style game that can...  
3  overall i hate mafiawerewolf but this version ...  
4  fun social deduction exercise that gets merrie...

## Drop Commenter and gameID

In [11]:
comments.drop(columns=['commenter', 'gameID'], inplace=True)

## Create a Dictionary of every word with its frequency

In [21]:
def create_count(comment):
    for x in comment.split(' '):
        if x in word_dictionary:
            word_dictionary[x] += 1
        else:
            word_dictionary[x] = 1
    return word_dictionary

In [33]:
%%time
word_dictionary = dict()
comments.comment.apply(create_count)

CPU times: user 13.4 s, sys: 525 ms, total: 14 s
Wall time: 14 s


In [36]:
word_dictionary

{'good': 142106,
 '': 1268570,
 'unique': 10304,
 'take': 31312,
 'on': 173501,
 'the': 1560992,
 'hidden': 6067,
 'role': 7607,
 'games': 143376,
 'and': 833047,
 'evil': 1586,
 'team': 4861,
 'win': 27673,
 'if': 112738,
 'they': 48130,
 'eliminate': 494,
 'each': 41510,
 'other': 65740,
 'where': 31856,
 'neutral': 631,
 'has': 81277,
 'objectives': 2148,
 'depending': 4230,
 'what': 68003,
 'was': 98404,
 'dealt': 1161,
 'bad': 24962,
 'component': 2621,
 'quality': 9785,
 'is': 549280,
 'lower': 2896,
 'end': 28146,
 'artwork': 13068,
 'lackluster': 329,
 'card': 61041,
 'stock': 2231,
 'flimsy': 419,
 'board': 45709,
 'design': 15571,
 'uninspired': 274,
 'playing': 79252,
 'this': 463479,
 'entertaining': 4234,
 'but': 374843,
 'its': 45123,
 'tough': 7061,
 'getting': 18428,
 'folks': 1971,
 'interested': 4969,
 'when': 70744,
 'newer': 1950,
 'have': 176728,
 'a': 999023,
 'much': 108750,
 'better': 64119,
 'graphical': 145,
 'presentation': 1090,
 'neat': 5886,
 'social': 460

In [37]:
len(word_dictionary)

246987

In [43]:
more_than_ten = {k: v for k, v in word_dictionary.items() if v > 10}
ten_or_less = {k: v for k, v in word_dictionary.items() if v <=10}

## Drop words that appear 10 or less times

In [40]:
print(len(more_than_ten))
print(len(ten_or_less))

27372
219615


In [41]:
%%time
sortedList=sorted(more_than_ten.values())
sorted_dict = dict()
for sortedKey in sortedList:
    for key, value in more_than_ten.items():
        if value==sortedKey:
            sorted_dict[key]=value

CPU times: user 2min, sys: 227 ms, total: 2min 1s
Wall time: 2min 1s


In [42]:
array_of_words = []
for key, value in sorted_dict.items():
    temp = [key,value]
    array_of_words.append(temp)

In [50]:
len(array_of_words)

27372

## Make reports of the frequency each word has in comments of different ratings

In [48]:
def word_count(comment, word, number):
    if word in comment.split(' '):
        if word in number:
            number[word] += comment.split(' ').count(word)
        else:
            number[word] = comment.split(' ').count(word)

In [92]:
def make_report(w, z, dictionary, dataframe):
    dict_list = dictionary
    testing_df = dataframe.copy()
    labels = ['word', 'average/std', 'percent_average', 'percent_std', 'rating', 'word_count', 'divisor', 'percent', 'time', 'type']
    to_return = pd.DataFrame(columns=labels)
    for word in dict_list[int(w):int(z)]:
        start_time = time.time()
        to_append = []
        std = 0
        average = 0
        for y in range(1,11):
            number = dict()
            testing_df.loc[testing_df.rating == y].comment.apply(word_count, word=word[0], number=number)
            divisor = testing_df.loc[testing_df.rating == y].comment.count()
            if word[0] in number:
                percent = number[word[0]]/divisor
            else:
                percent = 0
                number[word[0]] = 0
            to_append.append([word[0], None, None, None, y, number[word[0]], divisor, percent, None, 0])
        for_array = []
        for value in to_append:
            for_array.append(value[7])
        x = np.array(for_array)
        array1 = [[word[0], (np.sum(x)/10)/(np.std(x)), np.sum(x)/10, np.std(x), None, None, None, None, time.time()-start_time, 1]]
        for x in to_append:
            array1.append(x)
        inbetween_df = pd.DataFrame.from_records(array1, columns=labels)
        to_return = pd.concat([to_return, inbetween_df])
    return to_return

In [51]:
def write_csv(low, high, df, count):
    df.to_csv('new_report_for_{}_{}_to_{}.csv'.format(str(count).zfill(2), low, high))

In [52]:
def loop_write_report(dictionary, dataframe, number, count):
    num = int(number)
    size = int(count)
    first = 0
    counter = 0
    while first < num - 1:
        counter += 1
        if first + size < num - 2:
            report = make_report(first, first + size, dictionary, dataframe)
            write_csv(first, first + size, report, counter)
            print('dataframe written from {} to {}'.format(first, first + size))
            first = first + size + 1
        else:
            report = make_report(first, num - 1, dictionary, dataframe)
            write_csv(first, num - 1, report, counter)
            print('dataframe written from {} to {}'.format(first, num - 1))
            print('last dataframe')
            break

In [87]:
def loop_combine_reports_delete_old_reports(dictionary, dataframe, number, count):
    loop_write_report(dictionary, dataframe, number, count)
    glob_reports()    

In [74]:
def glob_reports():
    counter = 0
    df = pd.DataFrame()
    for report in glob.glob('new_report_for_*'):
        to_add = pd.read_csv(report)
        df = pd.concat([df, to_add])
        os.remove(report)
    df.to_csv('to_delete.csv')
        

In [94]:
len(array_of_words)

27372

In [95]:
loop_combine_reports_delete_old_reports(dictionary=array_of_words, dataframe=comments, number=len(array_of_words), count=100)

dataframe written from 0 to 100
dataframe written from 101 to 201
dataframe written from 202 to 302
dataframe written from 303 to 403
dataframe written from 404 to 504
dataframe written from 505 to 605
dataframe written from 606 to 706
dataframe written from 707 to 807
dataframe written from 808 to 908
dataframe written from 909 to 1009
dataframe written from 1010 to 1110
dataframe written from 1111 to 1211
dataframe written from 1212 to 1312
dataframe written from 1313 to 1413
dataframe written from 1414 to 1514
dataframe written from 1515 to 1615
dataframe written from 1616 to 1716
dataframe written from 1717 to 1817
dataframe written from 1818 to 1918
dataframe written from 1919 to 2019
dataframe written from 2020 to 2120
dataframe written from 2121 to 2221
dataframe written from 2222 to 2322
dataframe written from 2323 to 2423
dataframe written from 2424 to 2524
dataframe written from 2525 to 2625
dataframe written from 2626 to 2726
dataframe written from 2727 to 2827
dataframe wri

dataframe written from 22422 to 22522
dataframe written from 22523 to 22623
dataframe written from 22624 to 22724
dataframe written from 22725 to 22825
dataframe written from 22826 to 22926
dataframe written from 22927 to 23027
dataframe written from 23028 to 23128
dataframe written from 23129 to 23229
dataframe written from 23230 to 23330
dataframe written from 23331 to 23431
dataframe written from 23432 to 23532
dataframe written from 23533 to 23633
dataframe written from 23634 to 23734
dataframe written from 23735 to 23835
dataframe written from 23836 to 23936
dataframe written from 23937 to 24037
dataframe written from 24038 to 24138
dataframe written from 24139 to 24239
dataframe written from 24240 to 24340
dataframe written from 24341 to 24441
dataframe written from 24442 to 24542
dataframe written from 24543 to 24643
dataframe written from 24644 to 24744
dataframe written from 24745 to 24845
dataframe written from 24846 to 24946
dataframe written from 24947 to 25047
dataframe wr

In [3]:
wow = pd.read_csv('to_delete.csv')

In [102]:
wow.loc[wow.type == 1].loc[wow.loc[wow.type == 1]['average/std']<1.5].sort_values(by=['time'],ascending=False)

Unnamed: 0  Unnamed: 0.1                                       word  \
95447          847             0                                     lauded   
52734         1034             0                                 gloomhaven   
88484          484             0  bgcolor000000colorffffffsoloxcolorbgcolor   
226897         297             0                                  composite   
13134         1034             0                                      mists   
215787         187             0                                   deckpool   
182314         814             0                                       1944   
95557          957             0                                  wrenching   
95370          770             0                                      boast   
216084         484             0                                 lighthouse   
210408         308             0                                   daedalus   
268609         209             0                                    prairie   
135432         132             0                                    rabbits   
268719         319             0                                    viziers   
161161         561             0                                         ir   
211277          77             0                                  4-player-   
19910          110             0                                     inland   
154088          88             0                                 well-timed   
278014         814             0                                       kewl   
19943          143             0                                   mortgage   
165770         770             0                                  infinitum   
109813         913             0                                    everest   
165561         561             0                                       marc   
52712         1012             0                                     keltis   
268477          77             0                                  mystified   
225995         495             0                                   cold-war   
263725         825             0                                   avengers   
154396         396             0                                  lancaster   
40579          979             0                                       emdo   
225885         385             0                                       duet   
...            ...           ...                                        ...   
61644           44             0                                die-rolling   
61798          198             0                                   grateful   
123695         495             0                              werewolfmafia   
61743          143             0                              cat-and-mouse   
216051         451             0                                 blissfully   
123618         418             0                                  aquaretto   
62117          517             0                                   conveyor   
7304           704             0                                abomination   
185812        1012             0                               recollection   
123409         209             0                               accumulation   
62051          451             0                                  dictating   
7480           880             0                                snowballing   
246719         319             0                                discourages   
62656         1056             0                               brecommended   
215941         341             0                                     coupon   
62447          847             0                                intertwined   
123849         649             0                                hinterlands   
178156        1056             0                                not-so-good   
7634          1034             0                          

In [103]:
wow.loc[wow.word == '4-player-']

Unnamed: 0  Unnamed: 0.1       word  average/std  percent_average  \
211277          77             0  4-player-     0.333333         0.000005   
211278          78             1  4-player-          NaN              NaN   
211279          79             2  4-player-          NaN              NaN   
211280          80             3  4-player-          NaN              NaN   
211281          81             4  4-player-          NaN              NaN   
211282          82             5  4-player-          NaN              NaN   
211283          83             6  4-player-          NaN              NaN   
211284          84             7  4-player-          NaN              NaN   
211285          85             8  4-player-          NaN              NaN   
211286          86             9  4-player-          NaN              NaN   
211287          87            10  4-player-          NaN              NaN   

        percent_std  rating  word_count   divisor  percent         time  type  
211277     0.000015     NaN         NaN       NaN      NaN  2211.857467     1  
211278          NaN     1.0         0.0    3970.0  0.00000          NaN     0  
211279          NaN     2.0         0.0    8613.0  0.00000          NaN     0  
211280          NaN     3.0         0.0   16524.0  0.00000          NaN     0  
211281          NaN     4.0         0.0   29749.0  0.00000          NaN     0  
211282          NaN     5.0         0.0   52767.0  0.00000          NaN     0  
211283          NaN     6.0         0.0  110989.0  0.00000          NaN     0  
211284          NaN     7.0         0.0  197396.0  0.00000          NaN     0  
211285          NaN     8.0        11.0  222182.0  0.00005          NaN     0  
211286          NaN     9.0         0.0  131276.0  0.00000          NaN     0  
211287          NaN    10.0         0.0   68179.0  0.00000          NaN     0

In [2]:
df = pd.read_csv('to_delete.csv')
df.drop(columns=['Unnamed: 0'], inplace=True)
df['type'] = 0
df.loc[df.time>0, 'type'] = 1
df['normilization_divisor'] = 0
df['normilized_percent'] = 0
df['mean'] = 0
df['median'] = 0
df['mode'] = 0
df.drop(columns=['time'], inplace=True)

In [3]:
def write_normilization_divisor(series, df):
    numbers = []
    total = 0
    for x in series:
        if not math.isnan(x):
            numbers.append(x)
            total += x
    normilization_divisor = total
    df.loc[(df.word == series.name) & (df.type == 1),'normilization_divisor'] = normilization_divisor

In [7]:
%%time
df.groupby(df.word).percent.apply(write_normilization_divisor, df=df)

CPU times: user 18min 45s, sys: 21.4 s, total: 19min 6s
Wall time: 20min 6s


word
'           None
'04         None
'05         None
'06         None
'07         None
'08         None
'09         None
'1          None
'1'         None
'10         None
'10'        None
'11         None
'12         None
'13         None
'14         None
'15         None
'16         None
'17         None
'2'         None
'3'         None
'4'         None
'44         None
'5'         None
'6'         None
'7          None
'7'         None
'8'         None
'80s        None
'9'         None
'90s        None
            ... 
échange     None
überplay    None
į           None
žaidimas    None
žaidimo     None
ǝɥʇ         None
ʌv          None
–           None
—           None
“i          None
“take       None
”           None
•           None
…           None
€           None
−           None
≈           None
█           None
►           None
●           None
★★★★★       None
★★★★✰       None
★★★✰✰       None
★★✰✰✰       None
★✰✰✰✰       None
♥           None
✅           None
✔        

In [8]:
def normialize_percent(series, df):
    counter = 1
    for x in series:
        if not math.isnan(x):
            df.loc[(df.word == series.name) & (df.rating == counter), 'normilized_percent'] = x/(df.loc[(df.word == series.name) & (df.type == 1)]['normilization_divisor'].values[0])*100
            counter += 1
        print(series.name)

In [9]:
%%time
df.groupby(df.word).percent.apply(normialize_percent, df=df)

'
'
'
'
'
'
'
'
'
'
'
'04
'04
'04
'04
'04
'04
'04
'04
'04
'04
'04
'05
'05
'05
'05
'05
'05
'05
'05
'05
'05
'05
'06
'06
'06
'06
'06
'06
'06
'06
'06
'06
'06
'07
'07
'07
'07
'07
'07
'07
'07
'07
'07
'07
'08
'08
'08
'08
'08
'08
'08
'08
'08
'08
'08
'09
'09
'09
'09
'09
'09
'09
'09
'09
'09
'09
'1
'1
'1
'1
'1
'1
'1
'1
'1
'1
'1
'1'
'1'
'1'
'1'
'1'
'1'
'1'
'1'
'1'
'1'
'1'
'10
'10
'10
'10
'10
'10
'10
'10
'10
'10
'10
'10'
'10'
'10'
'10'
'10'
'10'
'10'
'10'
'10'
'10'
'10'
'11
'11
'11
'11
'11
'11
'11
'11
'11
'11
'11
'12
'12
'12
'12
'12
'12
'12
'12
'12
'12
'12
'13
'13
'13
'13
'13
'13
'13
'13
'13
'13
'13
'14
'14
'14
'14
'14
'14
'14
'14
'14
'14
'14
'15
'15
'15
'15
'15
'15
'15
'15
'15
'15
'15
'16
'16
'16
'16
'16
'16
'16
'16
'16
'16
'16
'17
'17
'17
'17
'17
'17
'17
'17
'17
'17
'17
'2'
'2'
'2'
'2'
'2'
'2'
'2'
'2'
'2'
'2'
'2'
'3'
'3'
'3'
'3'
'3'
'3'
'3'
'3'
'3'
'3'
'3'
'4'
'4'
'4'
'4'
'4'
'4'
'4'
'4'
'4'
'4'
'4'
'44
'44
'44
'44
'44
'44
'44
'44
'44
'44
'44
'5'
'5'
'5'
'5'
'5'
'5'
'5'
'5'
'5'
'5'
'5'
'6'
'6'
'6

'go
'go
'go
'go
'go
'go
'go'
'go'
'go'
'go'
'go'
'go'
'go'
'go'
'go'
'go'
'go'
'going
'going
'going
'going
'going
'going
'going
'going
'going
'going
'going
'good
'good
'good
'good
'good
'good
'good
'good
'good
'good
'good
'good'
'good'
'good'
'good'
'good'
'good'
'good'
'good'
'good'
'good'
'good'
'got
'got
'got
'got
'got
'got
'got
'got
'got
'got
'got
'got'
'got'
'got'
'got'
'got'
'got'
'got'
'got'
'got'
'got'
'got'
'gotcha'
'gotcha'
'gotcha'
'gotcha'
'gotcha'
'gotcha'
'gotcha'
'gotcha'
'gotcha'
'gotcha'
'gotcha'
'great'
'great'
'great'
'great'
'great'
'great'
'great'
'great'
'great'
'great'
'great'
'gric
'gric
'gric
'gric
'gric
'gric
'gric
'gric
'gric
'gric
'gric
'hand'
'hand'
'hand'
'hand'
'hand'
'hand'
'hand'
'hand'
'hand'
'hand'
'hand'
'heavy'
'heavy'
'heavy'
'heavy'
'heavy'
'heavy'
'heavy'
'heavy'
'heavy'
'heavy'
'heavy'
'hey
'hey
'hey
'hey
'hey
'hey
'hey
'hey
'hey
'hey
'hey
'hidden
'hidden
'hidden
'hidden
'hidden
'hidden
'hidden
'hidden
'hidden
'hidden
'hidden
'high
'high
'high
'

'samey'
'samey'
'samey'
'samey'
'samey'
'samey'
'samey'
'screw
'screw
'screw
'screw
'screw
'screw
'screw
'screw
'screw
'screw
'screw
'scripted'
'scripted'
'scripted'
'scripted'
'scripted'
'scripted'
'scripted'
'scripted'
'scripted'
'scripted'
'scripted'
'see'
'see'
'see'
'see'
'see'
'see'
'see'
'see'
'see'
'see'
'see'
'serious'
'serious'
'serious'
'serious'
'serious'
'serious'
'serious'
'serious'
'serious'
'serious'
'serious'
'small
'small
'small
'small
'small
'small
'small
'small
'small
'small
'small
'so
'so
'so
'so
'so
'so
'so
'so
'so
'so
'so
'solve'
'solve'
'solve'
'solve'
'solve'
'solve'
'solve'
'solve'
'solve'
'solve'
'solve'
'solved'
'solved'
'solved'
'solved'
'solved'
'solved'
'solved'
'solved'
'solved'
'solved'
'solved'
'special
'special
'special
'special
'special
'special
'special
'special
'special
'special
'special
'special'
'special'
'special'
'special'
'special'
'special'
'special'
'special'
'special'
'special'
'special'
'spiel
'spiel
'spiel
'spiel
'spiel
'spiel
'spiel
'spi

-------------------------
-------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
---------------------------
---------------------------
---------------------------
---------------------------
---------------------------
---------------------------
---------------------------
---------------------------
---------------------------
---------------------------
---------------------------
----------------------------
----------------------------
----------------------------
----------------------------
----------------------------
----------------------------
----------------------------
----------------------------
----------------------------
----------------------------
----------------------------
------------------------

------------------------------------------------------------jan
------------------------------------------------------------jan
------------------------------------------------------------jan
------------------------------------------------------------jan
-------------original
-------------original
-------------original
-------------original
-------------original
-------------original
-------------original
-------------original
-------------original
-------------original
-------------original
-------b
-------b
-------b
-------b
-------b
-------b
-------b
-------b
-------b
-------b
-------b
-------what-------
-------what-------
-------what-------
-------what-------
-------what-------
-------what-------
-------what-------
-------what-------
-------what-------
-------what-------
-------what-------
----0----
----0----
----0----
----0----
----0----
----0----
----0----
----0----
----0----
----0----
----0----
---b
---b
---b
---b
---b
---b
---b
---b
---b
---b
---b
---update---
---update---
---

...

wordphrase
wordphrase
wordplay
wordplay
wordplay
wordplay
wordplay
wordplay
wordplay
wordplay
wordplay
wordplay
wordplay
words
words
words
words
words
words
words
words
words
words
words
wordsu
wordsu
wordsu
wordsu
wordsu
wordsu
wordsu
wordsu
wordsu
wordsu
wordsu
wordy
wordy
wordy
wordy
wordy
wordy
wordy
wordy
wordy
wordy
wordy
wore
wore
wore
wore
wore
wore
wore
wore
wore
wore
wore
work
work
work
work
work
work
work
work
work
work
work
workable
workable
workable
workable
workable
workable
workable
workable
workable
workable
workable
workaround
workaround
workaround
workaround
workaround
workaround
workaround
workaround
workaround
workaround
workaround
workday
workday
workday
workday
workday
workday
workday
workday
workday
workday
workday
worked
worked
worked
worked
worked
worked
worked
worked
worked
worked
worked
worker
worker
worker
worker
worker
worker
worker
worker
worker
worker
worker
worker's
worker's
worker's
worker's
worker's
worker's
worker's
worker's
worker's
worker's
worker's

wrestle
wrestle
wrestle
wrestle
wrestle
wrestle
wrestle
wrestle
wrestle
wrestling
wrestling
wrestling
wrestling
wrestling
wrestling
wrestling
wrestling
wrestling
wrestling
wrestling
wretched
wretched
wretched
wretched
wretched
wretched
wretched
wretched
wretched
wretched
wretched
wright
wright
wright
wright
wright
wright
wright
wright
wright
wright
wright
wring
wring
wring
wring
wring
wring
wring
wring
wring
wring
wring
wrinkle
wrinkle
wrinkle
wrinkle
wrinkle
wrinkle
wrinkle
wrinkle
wrinkle
wrinkle
wrinkle
wrinkled
wrinkled
wrinkled
wrinkled
wrinkled
wrinkled
wrinkled
wrinkled
wrinkled
wrinkled
wrinkled
wrinkles
wrinkles
wrinkles
wrinkles
wrinkles
wrinkles
wrinkles
wrinkles
wrinkles
wrinkles
wrinkles
wrists
wrists
wrists
wrists
wrists
wrists
wrists
wrists
wrists
wrists
wrists
write
write
write
write
write
write
write
write
write
write
write
write-up
write-up
write-up
write-up
write-up
write-up
write-up
write-up
write-up
write-up
write-up
writen
writen
writen
writen
writen
writen
writen

yeesh
yeesh
yeesh
yeesh
yell
yell
yell
yell
yell
yell
yell
yell
yell
yell
yell
yelled
yelled
yelled
yelled
yelled
yelled
yelled
yelled
yelled
yelled
yelled
yelling
yelling
yelling
yelling
yelling
yelling
yelling
yelling
yelling
yelling
yelling
yellow
yellow
yellow
yellow
yellow
yellow
yellow
yellow
yellow
yellow
yellow
yellows
yellows
yellows
yellows
yellows
yellows
yellows
yellows
yellows
yellows
yellows
yells
yells
yells
yells
yells
yells
yells
yells
yells
yells
yells
yep
yep
yep
yep
yep
yep
yep
yep
yep
yep
yep
yer
yer
yer
yer
yer
yer
yer
yer
yer
yer
yer
yes
yes
yes
yes
yes
yes
yes
yes
yes
yes
yes
yesno
yesno
yesno
yesno
yesno
yesno
yesno
yesno
yesno
yesno
yesno
yesterday
yesterday
yesterday
yesterday
yesterday
yesterday
yesterday
yesterday
yesterday
yesterday
yesterday
yesteryear
yesteryear
yesteryear
yesteryear
yesteryear
yesteryear
yesteryear
yesteryear
yesteryear
yesteryear
yesteryear
yet
yet
yet
yet
yet
yet
yet
yet
yet
yet
yet
yggdrasil
yggdrasil
yggdrasil
yggdrasil
yggdrasil
yg

zillions
zillions
zillions
zillions
zillions
zillions
zillions
zimbabwe
zimbabwe
zimbabwe
zimbabwe
zimbabwe
zimbabwe
zimbabwe
zimbabwe
zimbabwe
zimbabwe
zimbabwe
zing
zing
zing
zing
zing
zing
zing
zing
zing
zing
zing
zip
zip
zip
zip
zip
zip
zip
zip
zip
zip
zip
ziploc
ziploc
ziploc
ziploc
ziploc
ziploc
ziploc
ziploc
ziploc
ziploc
ziploc
ziplock
ziplock
ziplock
ziplock
ziplock
ziplock
ziplock
ziplock
ziplock
ziplock
ziplock
zipped
zipped
zipped
zipped
zipped
zipped
zipped
zipped
zipped
zipped
zipped
zippy
zippy
zippy
zippy
zippy
zippy
zippy
zippy
zippy
zippy
zippy
zips
zips
zips
zips
zips
zips
zips
zips
zips
zips
zips
zman
zman
zman
zman
zman
zman
zman
zman
zman
zman
zman
zoch
zoch
zoch
zoch
zoch
zoch
zoch
zoch
zoch
zoch
zoch
zombicide
zombicide
zombicide
zombicide
zombicide
zombicide
zombicide
zombicide
zombicide
zombicide
zombicide
zombie
zombie
zombie
zombie
zombie
zombie
zombie
zombie
zombie
zombie
zombie
zombie's
zombie's
zombie's
zombie's
zombie's
zombie's
zombie's
zombie's
zombie'

word
'           None
'04         None
'05         None
'06         None
'07         None
'08         None
'09         None
'1          None
'1'         None
'10         None
'10'        None
'11         None
'12         None
'13         None
'14         None
'15         None
'16         None
'17         None
'2'         None
'3'         None
'4'         None
'44         None
'5'         None
'6'         None
'7          None
'7'         None
'8'         None
'80s        None
'9'         None
'90s        None
            ... 
échange     None
überplay    None
į           None
žaidimas    None
žaidimo     None
ǝɥʇ         None
ʌv          None
–           None
—           None
“i          None
“take       None
”           None
•           None
…           None
€           None
−           None
≈           None
█           None
►           None
●           None
★★★★★       None
★★★★✰       None
★★★✰✰       None
★★✰✰✰       None
★✰✰✰✰       None
♥           None
✅           None
✔        

In [49]:
def write_normialized_statistics(series, df):
    mean_total = 0
    median_total = 0
    mode_total = 0
    mode = 0
    counter = 0
    for x in series:
        if isinstance(x, (int, float)):
            mean_total += counter*x
            median_total += x
            if median_total >= 50:
                df.loc[(df.word == series.name) & (df.type == 1), 'median'] = counter
                median_total = -1
            if x > mode_total:
                mode_total = x
                mode = counter
            counter += 1
    df.loc[(df.word == series.name) & (df.type == 1), 'mean'] = mean_total/100
    df.loc[(df.word == series.name) & (df.type == 1), 'mode'] = mode

In [52]:
%%time
df.groupby(df.word).normilized_percent.apply(write_normialized_statistics, df=df)

CPU times: user 1h 2min, sys: 49.9 s, total: 1h 2min 50s
Wall time: 1h 5min 5s


word
'           None
'04         None
'05         None
'06         None
'07         None
'08         None
'09         None
'1          None
'1'         None
'10         None
'10'        None
'11         None
'12         None
'13         None
'14         None
'15         None
'16         None
'17         None
'2'         None
'3'         None
'4'         None
'44         None
'5'         None
'6'         None
'7          None
'7'         None
'8'         None
'80s        None
'9'         None
'90s        None
            ... 
échange     None
überplay    None
į           None
žaidimas    None
žaidimo     None
ǝɥʇ         None
ʌv          None
–           None
—           None
“i          None
“take       None
”           None
•           None
…           None
€           None
−           None
≈           None
█           None
►           None
●           None
★★★★★       None
★★★★✰       None
★★★✰✰       None
★★✰✰✰       None
★✰✰✰✰       None
♥           None
✅           None
✔        

In [54]:
df.head(11)

word  average/std  percent_average  percent_std  rating  word_count  \
0   rockets     1.644846         0.000045     0.000027     NaN         NaN   
1   rockets          NaN              NaN          NaN     1.0         0.0   
2   rockets          NaN              NaN          NaN     2.0         0.0   
3   rockets          NaN              NaN          NaN     3.0         1.0   
4   rockets          NaN              NaN          NaN     4.0         2.0   
5   rockets          NaN              NaN          NaN     5.0         1.0   
6   rockets          NaN              NaN          NaN     6.0         5.0   
7   rockets          NaN              NaN          NaN     7.0        10.0   
8   rockets          NaN              NaN          NaN     8.0        12.0   
9   rockets          NaN              NaN          NaN     9.0        10.0   
10  rockets          NaN              NaN          NaN    10.0         5.0   

     divisor   percent  type  normilization_divisor  normilized_percent  \
0        NaN       NaN     1               0.000446            0.000000   
1     3970.0  0.000000     0               0.000000            0.000000   
2     8613.0  0.000000     0               0.000000            0.000000   
3    16524.0  0.000061     0               0.000000           13.571225   
4    29749.0  0.000067     0               0.000000           15.076199   
5    52767.0  0.000019     0               0.000000            4.249833   
6   110989.0  0.000045     0               0.000000           10.102394   
7   197396.0  0.000051     0               0.000000           11.360459   
8   222182.0  0.000054     0               0.000000           12.111742   
9   131276.0  0.000076     0               0.000000           17.082401   
10   68179.0  0.000073     0               0.000000           16.445747   

        mean  median  mode  
0   6.774982       7     9  
1   0.000000       0     0  
2   0.000000       0     0  
3   0.000000       0     0  
4   0.000000       0     0  
5   0.000000       0     0  
6   0.000000       0     0  
7   0.000000       0     0  
8   0.000000       0     0  
9   0.000000       0     0  
10  0.000000       0     0

In [ ]:
df.to_csv('data_frame_with_normalized_statistics.csv')

In [3]:
df = pd.read_csv('data_frame_with_normalized_statistics.csv')

In [5]:
df.head()

Unnamed: 0     word  average/std  percent_average  percent_std  rating  \
0           0  rockets     1.644846         0.000045     0.000027     NaN   
1           1  rockets          NaN              NaN          NaN     1.0   
2           2  rockets          NaN              NaN          NaN     2.0   
3           3  rockets          NaN              NaN          NaN     3.0   
4           4  rockets          NaN              NaN          NaN     4.0   

   word_count  divisor   percent  type  normilization_divisor  \
0         NaN      NaN       NaN     1               0.000446   
1         0.0   3970.0  0.000000     0               0.000000   
2         0.0   8613.0  0.000000     0               0.000000   
3         1.0  16524.0  0.000061     0               0.000000   
4         2.0  29749.0  0.000067     0               0.000000   

   normilized_percent      mean  median  mode  
0            0.000000  6.774982       7     9  
1            0.000000  0.000000       0     0  
2            0.000000  0.000000       0     0  
3           13.571225  0.000000       0     0  
4           15.076199  0.000000       0     0

In [6]:
df['zeros'] = 0
df['total_word_count'] = 0
df.drop(columns=['Unnamed: 0'], inplace=True)

In [7]:
df.head()

word  average/std  percent_average  percent_std  rating  word_count  \
0  rockets     1.644846         0.000045     0.000027     NaN         NaN   
1  rockets          NaN              NaN          NaN     1.0         0.0   
2  rockets          NaN              NaN          NaN     2.0         0.0   
3  rockets          NaN              NaN          NaN     3.0         1.0   
4  rockets          NaN              NaN          NaN     4.0         2.0   

   divisor   percent  type  normilization_divisor  normilized_percent  \
0      NaN       NaN     1               0.000446            0.000000   
1   3970.0  0.000000     0               0.000000            0.000000   
2   8613.0  0.000000     0               0.000000            0.000000   
3  16524.0  0.000061     0               0.000000           13.571225   
4  29749.0  0.000067     0               0.000000           15.076199   

       mean  median  mode  zeros  total_word_count  
0  6.774982       7     9      0                 0  
1  0.000000       0     0      0                 0  
2  0.000000       0     0      0                 0  
3  0.000000       0     0      0                 0  
4  0.000000       0     0      0                 0

In [8]:
def values_with_zeros_and_total_word_count(series, df):
    counter = 0
    number_of_zeros = 0
    total_words = 0
    for x in series:
        if (counter > 0):
            if (x < 2):
                number_of_zeros += 1
            total_words += x
        counter +=1
    df.loc[(df.word == series.name) & (df.type == 1), 'zeros'] = number_of_zeros
    df.loc[(df.word == series.name) & (df.type == 1), 'total_word_count'] = total_words

In [ ]:
%%time
#run tonight
#df.groupby(df.word).word_count.apply(values_with_zeros_and_total_word_count, df=df)

In [9]:
df['large_percent_average'] = df.percent_average.apply(lambda x: x*10000)

In [10]:
df.to_csv('finished_analysis.csv')
df.loc[df.type == 1].to_csv('words.csv')

In [13]:
words = pd.read_csv('words.csv')
words.drop(columns=['Unnamed: 0'], inplace=True)

In [14]:
words.head()

word  average/std  percent_average  percent_std  rating  word_count  \
0      rockets     1.644846         0.000045     0.000027     NaN         NaN   
1     gangster     1.043339         0.000040     0.000038     NaN         NaN   
2     subjects     1.636259         0.000069     0.000042     NaN         NaN   
3  collaborate     1.153882         0.000075     0.000065     NaN         NaN   
4         gasp     1.209620         0.000042     0.000035     NaN         NaN   

   divisor  percent  type  normilization_divisor  normilized_percent  \
0      NaN      NaN     1               0.000446                 0.0   
1      NaN      NaN     1               0.000401                 0.0   
2      NaN      NaN     1               0.000693                 0.0   
3      NaN      NaN     1               0.000751                 0.0   
4      NaN      NaN     1               0.000421                 0.0   

       mean  median  mode  zeros  total_word_count  large_percent_average  
0  6.774982       7     9      0                 0               0.445929  
1  5.955222       6     4      0                 0               0.401268  
2  4.854628       5     3      0                 0               0.692759  
3  4.645202       4     1      0                 0               0.751058  
4  7.312834       7     6      0                 0               0.420928